In [1]:
from tensorflow.keras.utils import to_categorical
from sklearn.datasets import fetch_openml
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
import numpy as np
%matplotlib inline
seed = 0
np.random.seed(seed)
import tensorflow as tf
tf.random.set_seed(seed)
import os


import pandas as pd
import seaborn as sb
import matplotlib.pyplot as plt
from callbacks import all_callbacks

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, BatchNormalization
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.regularizers import l1

from qkeras.qlayers import QDense, QActivation
from qkeras.quantizers import quantized_bits, quantized_relu
import tensorflow.compat.v1 as tf1

2022-12-15 15:15:15.989206: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2022-12-15 15:15:16.171317: I tensorflow/core/util/util.cc:169] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2022-12-15 15:15:16.179010: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/xilinx/xrt/lib:
2022-12-15 15:15:16.179027: I tensorflow/stream_executor/cuda/cudart_stub.c

## Fetch the pendigits dataset

In [2]:
df = pd.read_csv('./pendigits.csv', sep = ',')
print (np.shape(df))
df

(10992, 17)


input1  input2  input3  input4  input5  input6  input7  input8  input9  \
0          47     100      27      81      57      37      26       0       0   
1           0      89      27     100      42      75      29      45      15   
2           0      57      31      68      72      90     100     100      76   
3           0     100       7      92       5      68      19      45      86   
4           0      67      49      83     100     100      81      80      60   
...       ...     ...     ...     ...     ...     ...     ...     ...     ...   
10987      36     100      24      70       0      38      49      33      95   
10988      16      75      41     100      52      64      32      27       0   
10989      56     100      27      79       0      39      12       0      66   
10990      19     100       0      61       3      23      48       0      97   
10991      38     100      37      81      12      55       0      28      52   

       input10  input11  input12  input13  input14  input15  input16  Y  
0           23       56       53      100       90       40       98  8  
1           15       37        0       69        2      100        6  2  
2           75       50       51       28       25       16        0  1  
3           34      100       45       74       23       67        0  4  
4           60       40       40       33       20       47        0  1  
...        ...      ...      ...      ...      ...      ...      ... ..  
10987       47       87       55       96       21      100        0  4  
10988        0       21        9       62        2      100       14  2  
10989       15      100       51       93       93       38       93  0  
10990       27      100       66       62       97       10       81  0  
10991       27      100       42       86       26       65        0  4  

[10992 rows x 17 columns]

In [3]:
X = df.drop('Y', axis = 1).values

0        8
1        2
2        1
3        4
4        1
        ..
10987    4
10988    2
10989    0
10990    0
10991    4
Name: Y, Length: 10992, dtype: int64


In [5]:
le = LabelEncoder()
print(y)
y = le.fit_transform(y)
print(le.classes_)
y = to_categorical(y, 10)
print(y)

0        8
1        2
2        1
3        4
4        1
        ..
10987    4
10988    2
10989    0
10990    0
10991    4
Name: Y, Length: 10992, dtype: int64
[0 1 2 3 4 5 6 7 8 9]
[[0. 0. 0. ... 0. 1. 0.]
 [0. 0. 1. ... 0. 0. 0.]
 [0. 1. 0. ... 0. 0. 0.]
 ...
 [1. 0. 0. ... 0. 0. 0.]
 [1. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


In [8]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
X_train,X_test,Y_train,Y_test = train_test_split(X,y,test_size=0.3,random_state=42)
sc = MinMaxScaler(feature_range=(0,0.9))
X_train = sc.fit_transform(X_train)
X_test = sc.transform(X_test)

In [10]:
ls=np.argmax(Y_test,axis=1)
print(ls)
#np.savetxt('output_classes.dat',ls, fmt='%d')

[0 6 1 ... 5 7 1]


In [12]:
print("Shape of X_train: ",X_train.shape)
print("Shape of X_test: ", X_test.shape)
print("Shape of y_train: ",Y_train.shape)
print("Shape of y_test",Y_test.shape)

Shape of X_train:  (7694, 16)
Shape of X_test:  (3298, 16)
Shape of y_train:  (7694, 10)
Shape of y_test (3298, 10)


In [14]:
import pickle
from joblib import load, dump
loaded_model = load('./Pendigits.MLP_clf.joblib')

/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/sklearn/base.py:329: UserWarning: Trying to unpickle estimator LabelBinarizer from version 0.24.2 when using version 1.1.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/sklearn/base.py:329: UserWarning: Trying to unpickle estimator MLPClassifier from version 0.24.2 when using version 1.1.2. This might lead to breaking code or invalid results. Use at your own risk. For more info please refer to:
https://scikit-learn.org/stable/model_persistence.html#security-maintainability-limitations
  warnings.warn(


In [18]:
w1=loaded_model.coefs_[0]
b1=loaded_model.intercepts_[0]
w2=loaded_model.coefs_[1]
b2=loaded_model.intercepts_[1]

In [19]:
wb1=[]
wb1.append(w1)
wb1.append(b1)

wb2=[]
wb2.append(w2)
wb2.append(b2)

In [26]:
from tensorflow.keras.utils import to_categorical
from sklearn.datasets import fetch_openml
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler
import numpy as np

import tensorflow as tf
import os
import pandas as pd
import seaborn as sb

from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Activation, BatchNormalization
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.regularizers import l1
from callbacks import all_callbacks
from qkeras.qlayers import QDense, QActivation
from qkeras.quantizers import quantized_bits, quantized_relu
import tensorflow.compat.v1 as tf1
from tensorflow_model_optimization.python.core.sparsity.keras import prune, pruning_callbacks, pruning_schedule
from tensorflow_model_optimization.sparsity.keras import strip_pruning
from qkeras.utils import model_save_quantized_weights
from sklearn.preprocessing import MinMaxScaler
import hls4ml
import write_mlp_mergemult_ps as wv

/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/hls4ml/converters/__init__.py:16: UserWarning: WARNING: Pytorch converter is not enabled!
  warnings.warn("WARNING: Pytorch converter is not enabled!")


### genetic algorithm to determine the relu size, weight size, bias size and sparsity

In [27]:
import blackbox as bb
from pymoo.algorithms.moo.nsga2 import NSGA2
from pymoo.operators.crossover.sbx import SBX
from pymoo.operators.mutation.pm import PM
from pymoo.operators.sampling.rnd import IntegerRandomSampling
from pymoo.core.problem import ElementwiseProblem
from pymoo.operators.repair.rounding import RoundingRepair
import area as ar
from importlib import reload
reload(bb)
reload(ar)

<module 'area' from '/home/argykokk/Desktop/TC/genetic_pendigits/area.py'>

In [28]:
class MyProblem(ElementwiseProblem):

    def __init__(self,weightsbiases1,weightsbiases2,layer1,layer2,layer3,X_test,X_train,Y_test,Y_train):
        self.weightsbiases1=weightsbiases1
        self.weightsbiases2=weightsbiases2
        self.layer1=layer1
        self.layer2=layer2
        self.layer3=layer3
        self.X_test=X_test
        self.X_train=X_train
        self.Y_test=Y_test
        self.Y_train=Y_train
        #x[0]: relu_size
        #x[1]: weight size layer1
        #x[2]: bias size layer1
        #x[3]: weight size layer2
        #x[4]: bias size layer2
        #x[5]: pruning sparsity
        #x[6]: input size
        #x[7]: int relu size
        #x[8]: int w1 size
        #x[9]: int b1 size
        #x[10]: int w2 size
        #x[11]: int b2 size
        
        super().__init__(n_var=12,
                         n_obj=2,
                         n_ieq_constr=0,
                         xl=np.array([4,3,2,3,2,0,2,0,0,0,0,0]),
                         xu=np.array([8,7,5,7,5,8,4,2,2,1,2,1]),
                         vtype=int)

    def _evaluate(self, x, out, *args, **kwargs):
        accuracy, weights = bb.blackbox(self.weightsbiases1,self.weightsbiases2, x[0], x[1], x[2], x[3], x[4], x[5], x[6] , x[7], x[8], x[9], x[10], x[11],  self.layer1, self.layer2, self.layer3, self.X_test, self.Y_test, self.X_train, self.Y_train)
        f1 = 1- accuracy
        f2 = ar.area(weights,x[6],x[0],x[1],x[3], x[8], x[10], self.layer1,self.layer2,self.layer3)

        out["F"] = [f1, f2]


In [29]:
layer1=16
layer2=5
layer3=10
problem = MyProblem(wb1,wb2,layer1,layer2,layer3,X_test,X_train,Y_test,Y_train)

In [30]:
algorithm = NSGA2(
    pop_size=100,
    n_offsprings=50,
    sampling=IntegerRandomSampling(),
    crossover=SBX(vtype=float, repair=RoundingRepair()),
    mutation=PM( vtype=float, repair=RoundingRepair()),
    eliminate_duplicates=True
)

In [31]:
from pymoo.termination import get_termination

termination = get_termination("n_gen",50)

In [ ]:
%%time
from pymoo.optimize import minimize

res = minimize(problem,
               algorithm,
               termination,
               seed=1,
               save_history=True,
               verbose=True)
X = res.X
F = res.F

### plot all the solutions from the final generation

In [ ]:
paretos=res.X

In [ ]:
from pymoo.visualization.scatter import Scatter
pop=res.pop
vals=pop.get("F")
plot = Scatter()
plot.add(problem.pareto_front(), plot_type="line", color="black", alpha=0.7)
plot.add(res.F, facecolor="none", edgecolor="red")
plot.show()

### plot the pareto solutions from the final generation

In [ ]:
plot = Scatter()
plot.add(problem.pareto_front(), plot_type="line", color="black", alpha=0.7)
plot.add(res.F, facecolor="none", edgecolor="blue")
plot.show()

In [ ]:
# import pickle
# with open("paretos_pendigits", "wb") as fp:   #Pickling
#     pickle.dump(paretos, fp)
# with open("costs_pendigits", "wb") as fp:   #Pickling
#     pickle.dump(costs, fp)

In [ ]:
import pickle
with open("paretos_pendigits", "rb") as fp:   # Unpickling
    paretos = pickle.load(fp)
with open("costs_pendigits", "rb") as fp:   # Unpickling
    costs = pickle.load(fp)

In [32]:
import pareto_verilogs as pv
import pareto_clustering_verilogs as pcv
import only_pruning_verilog as opv
from importlib import reload

reload(pv)
reload(pcv)
reload(opv)

<module 'only_pruning_verilog' from '/home/argykokk/Desktop/TC/genetic_pendigits/only_pruning_verilog.py'>

In [33]:
i=0
layer1=16
layer2=5
layer3=10
epochs=1
lr=0.001
opv.generate(i,layer1,layer2,layer3,lr,epochs,X_train,Y_train,X_test,Y_test,wb1,wb2)

In [ ]:
i=0
for solution in true_paretos:
    print("solution is"+str(solution))
    relusize_f=solution[0]
    weight_size_f1=solution[1]
    bias_size_f1=solution[2]
    weight_size_f2=solution[3]
    bias_size_f2=solution[4]
    sparsity=solution[5]
    inputsize=solution[6]
    relusize_int=solution[7]
    w1_int=solution[8]
    b1_int=solution[9]
    w2_int=solution[10]
    b2_int=solution[11]
    model=pv.generate(i,relusize_f,weight_size_f1,bias_size_f1,weight_size_f2,bias_size_f2,sparsity,inputsize,relusize_int,w1_int,b1_int,w2_int,b2_int,layer1,layer2,layer3,lr,epochs,X_train,Y_train,X_test,Y_test,wb1,wb2)
    i += 1

In [ ]:
# import pickle
# with open("true_paretos_pendigits", "wb") as fp:   #Pickling
#     pickle.dump(true_paretos, fp)
# with open("true_paretos_accuracy_pendigits", "wb") as fp:   #Pickling
#     pickle.dump(accuracy_list, fp)
# with open("true_paretos_weights_pendigits", "wb") as fp:   #Pickling
#     pickle.dump(weights_list, fp)

In [34]:
import pickle
with open("true_paretos_pendigits", "rb") as fp:   # Unpickling
    true_paretos = pickle.load(fp)
with open("true_paretos_accuracy_pendigits", "rb") as fp:   # Unpickling
    true_accuracy_list = pickle.load(fp)
with open("true_paretos_weights_pendigits", "rb") as fp:   # Unpickling
    true_weights_list = pickle.load(fp)

2022-12-15 15:15:30.362002: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/xilinx/xrt/lib:
2022-12-15 15:15:30.362145: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublas.so.11'; dlerror: libcublas.so.11: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/xilinx/xrt/lib:
2022-12-15 15:15:30.362241: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcublasLt.so.11'; dlerror: libcublasLt.so.11: cannot open shared object file: No such file or directory; LD_LIBRARY_PATH: /opt/xilinx/xrt/lib:
2022-12-15 15:15:30.362339: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcufft.so.10'; dlerror: libcufft.so.10: cannot open shared object file:

### pareto custom clustering

In [ ]:
#x[0]: relu_size
#x[1]: weight size layer1
#x[2]: bias size layer1
#x[3]: weight size layer2
#x[4]: bias size layer2
#x[5]: pruning sparsity
#x[6]: input size
#x[7]: int relu size
#x[8]: int w1 size
#x[9]: int b1 size
#x[10]: int w2 size
#x[11]: int b2 size

In [49]:
import pareto_sharing as ps

In [50]:
for w in range(0,len(true_paretos)):
    reload(ps)
    relu= int(true_paretos[w][0])
    bits_l1= int(true_paretos[w][1])
    bias_l1= int(true_paretos[w][2])
    bits_l2=  int(true_paretos[w][3])
    bias_l2=  int(true_paretos[w][4])
    input_s= int(true_paretos[w][6])
    relu_int = int(true_paretos[w][7]) + 1
    bits_int_l1= int(true_paretos[w][8]) + 1
    bias_int_l1=int(true_paretos[w][9]) + 1
    bits_int_l2 = int(true_paretos[w][10]) + 1
    bias_int_l2 = int(true_paretos[w][11]) + 1
    layer1=16
    layer2=5
    layer3-10

    window=0
    for i in range(1,layer2+1):
        for j in range(1,layer3+1):
            c1 = i
            c2 = j
            ps.top_sharing(w,true_weights_list[w], bits_l1, bits_int_l1, bits_l2, bits_int_l2, bias_l1, bias_int_l1, bias_l2, bias_int_l2, input_s, relu, relu_int, X_test, Y_test, layer1, layer2, layer3, c1, c2, window)
    window=2
    for i in range(1,layer2+1):
        for j in range(1,layer3+1):
            c1 = i
            c2 = j
            ps.top_sharing(w,true_weights_list[w], bits_l1, bits_int_l1, bits_l2, bits_int_l2, bias_l1, bias_int_l1, bias_l2, bias_int_l2, input_s, relu, relu_int, X_test, Y_test, layer1, layer2, layer3, c1, c2, window)  

/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


104/104 [==============================] - 1s 1ms/step - loss: 4.0411 - accuracy: 0.2780
accuracy = 0.2780472934246063
Interpreting Sequential
Topology:
Layer name: fc1_input, layer type: Input
Layer name: fc1, layer type: QDense
Layer name: relu1, layer type: QActivation
Layer name: output, layer type: QDense
Layer name: softmax, layer type: Activation
copy top.v, sim.Xtest, and sim.Ytest to the synopsys project 


/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


104/104 [==============================] - 0s 1ms/step - loss: 2.2835 - accuracy: 0.4518
accuracy = 0.4517889618873596
Interpreting Sequential
Topology:
Layer name: fc1_input, layer type: Input
Layer name: fc1, layer type: QDense
Layer name: relu1, layer type: QActivation
Layer name: output, layer type: QDense
Layer name: softmax, layer type: Activation
copy top.v, sim.Xtest, and sim.Ytest to the synopsys project 


/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)
/home/argykokk/Desktop/TC/genetic_pendigits/pareto_sharing.py:173: ConvergenceWarning: Number of distinct clusters (2) found smaller than n_clusters (3). Possibly due to duplicate points in X.
  # calculate the estimated area overhead of this centroid
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


...

frozen dataset 0
frozen dataset 1
frozen dataset 2
frozen dataset 3
frozen dataset 4
frozen dataset 5
frozen dataset 6
frozen dataset 7
frozen dataset 9
frozen dataset 11
frozen dataset 12
frozen dataset 14
frozen dataset 0
frozen dataset 1
frozen dataset 3


/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)


104/104 [==============================] - 0s 1ms/step - loss: 1.9831 - accuracy: 0.2726
accuracy = 0.27258944511413574
Interpreting Sequential
Topology:
Layer name: fc1_input, layer type: Input
Layer name: fc1, layer type: QDense
Layer name: relu1, layer type: QActivation
Layer name: output, layer type: QDense
Layer name: softmax, layer type: Activation
copy top.v, sim.Xtest, and sim.Ytest to the synopsys project 


/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/initializers/initializers_v2.py:120: UserWarning: The initializer LecunUniform is unseeded and being called multiple times, which will return identical values  each time (even if the initializer is unseeded). Please update your code to provide a seed to the initializer, or avoid using the same initalizer instance more than once.
  warnings.warn(
/home/argykokk/Desktop/TC/genetic_pendigits/pareto_sharing.py:173: ConvergenceWarning: Number of distinct clusters (1) found smaller than n_clusters (2). Possibly due to duplicate points in X.
  # calculate the estimated area overhead of this centroid
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers/optimizer_v2/adam.py:114: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super().__init__(name, **kwargs)
/home/argykokk/miniconda3/envs/hls4ml-tutorial/lib/python3.8/site-packages/keras/optimizers

frozen dataset 0
frozen dataset 1
frozen dataset 2
frozen dataset 3
frozen dataset 4
frozen dataset 5
frozen dataset 6
frozen dataset 7
frozen dataset 9
frozen dataset 11
frozen dataset 12
frozen dataset 14
frozen dataset 0
frozen dataset 1
frozen dataset 3
104/104 [==============================] - 0s 961us/step - loss: 1.9831 - accuracy: 0.2726
accuracy = 0.27258944511413574
Interpreting Sequential
Topology:
Layer name: fc1_input, layer type: Input
Layer name: fc1, layer type: QDense
Layer name: relu1, layer type: QActivation
Layer name: output, layer type: QDense
Layer name: softmax, layer type: Activation
copy top.v, sim.Xtest, and sim.Ytest to the synopsys project 
